In [88]:
import pandas as pd
import numpy as np
from datetime import timedelta
import keras
from keras.utils import np_utils
from keras.models import Sequential
from keras.layers import LSTM, Dense, Dropout, LeakyReLU, Flatten
from keras.callbacks import ModelCheckpoint

In [89]:
prod_data_train = pd.read_csv('production_data_train.csv')
prod_data_test = pd.read_csv('production_data_test.csv')
ihs_data = pd.read_csv('IHS_data.csv')
harmony_data = pd.read_csv('Harmony_data.csv')
test_apis = pd.read_csv('test_APIs.csv', header=None)
test_apis.columns = ['API']
test_apis['API'] = (test_apis['API']).astype(str)
test_apis['API'] = test_apis['API'].apply(lambda x: x.zfill(14))
sample_file = pd.read_csv('sample_file.csv')    

In [90]:
def preprocess(prod_data, wells_data):
    prod_data = prod_data.drop_duplicates(subset=['API', 'Month', 'Year'], keep='last', inplace=False)
    
    # adding zeros to API
    prod_data['API'] = (prod_data['API']).astype(str)
    prod_data['API'] = prod_data['API'].apply(lambda x: x.zfill(14))
    
    # adding zeros to API
    wells_data['API'] = (wells_data['API']).astype(str)
    wells_data['API'] = wells_data['API'].apply(lambda x: x.zfill(14))
    
    # storing peak records 
    idx_max = prod_data.groupby(['API'])['Liquid'].transform('max') == prod_data['Liquid']
    max_month_prod_data = prod_data[idx_max].drop_duplicates(subset='API', keep='first', inplace=False)
    list_indices = ['API', 'Year', 'Month', 'Liquid']
    max_month_prod_data = max_month_prod_data[list_indices]
    max_month_prod_data = max_month_prod_data.rename(columns={"Year": "Max_Year", "Month": "Max_Month", "Liquid": "Max_Liquid"})
    
    # merging the two dataframes to get max month and max year
    new_prod_data_orig = prod_data.merge(max_month_prod_data, on='API')
    
    # Remove Pre-Peak Months (clean up)
    new_prod_data = new_prod_data_orig[((new_prod_data_orig['Year'] == new_prod_data_orig['Max_Year']))]
    new_prod_data = new_prod_data[(new_prod_data['Month'] >= new_prod_data['Max_Month'])]

    new_prod_data2 = new_prod_data_orig[((new_prod_data_orig['Year'] > new_prod_data_orig['Max_Year']))]
    new_prod_data3 = new_prod_data.append(new_prod_data2)
    
    # adding month index column to post peak production data
    new_prod_data3['index'] = calc_month_index(new_prod_data3['Max_Year'], new_prod_data3['Max_Month'], new_prod_data3['Year'], new_prod_data3['Month'])
    indexed_prod_data = new_prod_data3
    
    # removed nullified SpudDates and CompletionDates
    wells_data = wells_data[~((wells_data['SpudDate'].isnull()) & (wells_data['CompletionDate'].isnull()))]
    
    # replacing null CompletionDates with SpudDates + six months
    wells_data['SpudDate'] = pd.to_datetime(wells_data['SpudDate'])
    wells_data['CompletionDate'] = pd.to_datetime(wells_data['CompletionDate'])
    wells_data.loc[wells_data['CompletionDate'].isnull(), 'CompletionDate'] = wells_data['SpudDate'] + timedelta(days=170) 
    
    # replacing StateNames with indices
    unique_state_names = wells_data.StateName.unique()
    unique_state_ids = list(range(0, len(unique_state_names)))
    dict_state_names = dict(zip( unique_state_names, unique_state_ids))
    wells_data['StateName'] = wells_data['StateName'].map(dict_state_names)
                            
    # replacing CountyNames with indices                         
    unique_county_names = wells_data.CountyName.unique()
    unique_county_ids = list(range(0, len(unique_county_names)))
    dict_county_names = dict(zip(unique_county_names, unique_county_ids))
    wells_data['CountyName'] = wells_data['CountyName'].map(dict_county_names)
    
    # replacing BasinName with indices
    unique_basin_names = wells_data.BasinName.unique()
    unique_basin_ids = list(range(0, len(unique_basin_names)))
    dict_basin_names = dict(zip(unique_basin_names, unique_basin_ids))
    wells_data['BasinName'] = wells_data['BasinName'].map(dict_basin_names)
    
    #replacing Formation with indices
    unique_formation_names = wells_data.formation.unique()
    unique_formation_ids = list(range(0, len(unique_formation_names)))
    dict_formation_names = dict(zip(unique_formation_names, unique_formation_ids))
    wells_data['formation'] = wells_data['formation'].map(dict_formation_names)
        
#     wells_data[wells_data['CompletionDate'] >= pd.Timestamp(2014, 1 , 1)]['CompletionDate'] = 1  
#     wells_data[wells_data['CompletionDate'] !=  1]['CompletionDate'] = 0 
#     print(wells_data[wells_data['CompletionDate'] < pd.Timestamp(2014, 1 , 1)])

    indexed_prod_data = indexed_prod_data.merge(wells_data, on='API')
    print
    three_years_data = indexed_prod_data[(indexed_prod_data['Max_Year'] < 2016) |((indexed_prod_data['Max_Year'] == 2016) & (indexed_prod_data['Max_Month'] == 1))] 
    three_years_data = three_years_data[three_years_data['index'] <= 35] 
    
    return three_years_data

In [91]:
# calculates month index
def calc_month_index(max_year, max_month, year, month):
    return (12 - max_month + (year - max_year - 1)*12 + month) * (year != max_year) + (year == max_year) * (month - max_month) + 1 

In [92]:
processed_train = preprocess(prod_data_train, ihs_data)
processed_test = preprocess(prod_data_test, ihs_data)

harmony_data['API'] = (harmony_data['API']).astype(str)
harmony_data['API'] = harmony_data['API'].apply(lambda x: x.zfill(14))

harmony_data[harmony_data['WATER_PER_FOOT'].isnull()] = 0
harmony_data[harmony_data['PROP_PER_FOOT'].isnull()] = 0

complete_prod_train = processed_train.merge(harmony_data, on='API')
complete_prod_test = processed_test.merge(harmony_data, on='API')
complete_prod_test = complete_prod_test.merge(test_apis, on='API')

# removing production of month index greater that 3
complete_prod_test = complete_prod_test[complete_prod_test['index'] <= 3]

# replacing gor nans with zeros
complete_prod_train[complete_prod_train['GOR_30'].isnull()]=0
complete_prod_train[complete_prod_train['GOR_60'].isnull()]=0
complete_prod_train[complete_prod_train['GOR_90'].isnull()]=0


C:\Users\Dell\Anaconda2\envs\py36\lib\site-packages\ipykernel\__main__.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
C:\Users\Dell\Anaconda2\envs\py36\lib\site-packages\ipykernel\__main__.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


In [93]:
cols_train = ['Year', 'Month', 'Gas', 'Water', 'Max_Year','operatorNameIHS', 'CompletionDate', 'FirstProductionDate', 'Max_Liquid', 'Max_Month', 'SpudDate', 'PermitDate', '_LastUpdate']
cols_test = ['Year', 'Month', 'Gas', 'date', 'Water', 'Max_Year','operatorNameIHS', 'CompletionDate', 'FirstProductionDate', 'Max_Liquid', 'Max_Month', 'SpudDate', 'PermitDate', '_LastUpdate']
complete_prod_train = complete_prod_train.drop(cols_train, axis=1)
complete_prod_test = complete_prod_test.drop(cols_test, axis=1)

In [94]:
col_headers = list(complete_prod_train)
col_headers = col_headers[1:]
min_train_feat_array = []
min_test_feat_array = []
max_train_feat_array = []
max_test_feat_array = []
mean_train_feat_arr = []
std_train_feat_arr = []
mean_test_feat_arr = []
std_test_feat_arr = []
for header in col_headers:
    mean_train_feat_arr.append((complete_prod_train[header]).mean())
    std_train_feat_arr.append(complete_prod_train[header].std())
    mean_test_feat_arr.append(complete_prod_test[header].mean())
    std_test_feat_arr.append(complete_prod_test[header].std())
    min_train_feat_array.append(complete_prod_train[header].min())
    min_test_feat_array.append(complete_prod_test[header].min())
    max_train_feat_array.append(complete_prod_train[header].max())
    max_test_feat_array.append(complete_prod_test[header].max())

mean_train_feat_arr = np.array(mean_train_feat_arr)
std_train_feat_arr = np.array(std_train_feat_arr)
mean_test_feat_arr = np.array(mean_test_feat_arr)
std_test_feat_arr = np.array(std_test_feat_arr)
mean_test_feat_arr[4] = 18.0
std_test_feat_arr[4] = 10.1
min_train_feat_array = np.array(min_train_feat_array)
min_test_feat_array = np.array(min_test_feat_array)
max_train_feat_array = np.array(max_train_feat_array)
max_test_feat_array = np.array(max_test_feat_array)

In [63]:
counter_global = 0
def data_prep(prod_data, arr_inp, arr_out, mean_arr, std_arr, apis_arr):
    prod_data = prod_data.groupby('API').apply(generate_input, arr_inp, arr_out, mean_arr, std_arr, apis_arr)
    

In [99]:
def generate_input(group, arr_inp, arr_out, mean_arr, std_arr, apis_arr):
    global counter_global 
    cols_rem = ['API']
    group2 = np.array(group)
    group = group.drop(cols_rem, axis = 1)
#     print(group['index'])
    group = np.array(group)
    if(len(group)<3):
        counter_global +=1
#         print(apis_arr[-1], len(group))
    for i in range(len(group)):
        group[i] = ((group[i]) - mean_arr)/(std_arr)
    if len(group) >= 36:
        for i in range(len(group) - 3):
            cur_part = group[i:i+3]
            cur_shift = group[i+3, 0:4]
            arr_inp.append(list(cur_part))
            arr_out += (list(cur_shift))
    elif len(group) >= 3:
        apis_arr.append(group2[0, 0])
        for i in range(len(group) - 2):
            cur_part = group[i:i+3]
            arr_inp.append(list(cur_part))
            cur_shift = []
            if i == len(group) - 3:
                cur_shift = ([0,0,0,0])
            else:
                cur_shift = list(group[i+3, 0:4])
            arr_out += (cur_shift)
            

In [85]:
#generating the datasets
X_train = []
X_test = []
Y_train = []
Y_test = []
data_prep(complete_prod_train, X_train, Y_train, mean_train_feat_arr, std_train_feat_arr, [])
testing_apis = []
counter_global = 0
data_prep(complete_prod_test, X_test, Y_test, mean_test_feat_arr, std_test_feat_arr, testing_apis)

136866    0
136867    0
136868    0
136869    0
136870    0
136871    0
136872    0
136873    0
136874    0
136875    0
136876    0
136877    0
136878    0
136879    0
136880    0
136881    0
136882    0
136883    0
136884    0
136885    0
136886    0
136887    0
136888    0
136889    0
136890    0
136891    0
136892    0
136893    0
136894    0
136895    0
         ..
260337    0
260338    0
260339    0
260340    0
260341    0
260342    0
260343    0
260344    0
260345    0
260346    0
260347    0
260348    0
260349    0
260350    0
260351    0
260352    0
260353    0
260354    0
260355    0
260356    0
260357    0
260358    0
260359    0
260360    0
260361    0
260362    0
260363    0
260364    0
260365    0
260366    0
Name: index, Length: 4089, dtype: int64
136866    0
136867    0
136868    0
136869    0
136870    0
136871    0
136872    0
136873    0
136874    0
136875    0
136876    0
136877    0
136878    0
136879    0
136880    0
136881    0
136882    0
136883    0
136884    0


Name: index, dtype: int64
73326     1
73327     2
73328     3
73329     4
73330     5
73331     6
73332     7
73333     8
73334     9
73335    10
73336    11
73337    12
73338    13
73339    14
73340    15
73341    16
73342    17
73343    18
73344    19
73345    20
73346    21
73347    22
73348    23
73349    24
73350    25
73351    26
73352    27
73353    28
73354    29
73355    30
73356    31
73357    32
73358    33
73359    34
73360    35
73361    36
Name: index, dtype: int64
41718     1
41719     2
41720     3
41721     4
41722     5
41723     6
41724     7
41725     8
41726     9
41727    10
41728    11
41729    12
41730    13
41731    14
41732    15
41733    16
41734    17
41735    18
41736    19
41737    20
41738    21
41739    22
41740    23
41741    24
41742    25
41743    26
41744    27
41745    28
41746    29
41747    30
41748    31
41749    32
41750    33
41751    34
41752    35
41753    36
Name: index, dtype: int64
45966     1
45967     2
45968     3
45969     4
45970     

121818     1
121819     2
121820     3
121821     4
121822     5
121823     6
121824     7
121825     8
121826     9
121827    10
121828    11
121829    12
121830    13
121831    14
121832    15
121833    16
121834    17
121835    18
121836    19
121837    20
121838    21
121839    22
121840    23
121841    24
121842    25
121843    26
121844    27
121845    28
121846    29
121847    30
121848    31
121849    32
121850    33
121851    34
121852    35
121853    36
Name: index, dtype: int64
10326     1
10327     2
10328     3
10329     4
10330     5
10331     6
10332     7
10333     8
10334     9
10335    10
10336    11
10337    12
10338    13
10339    14
10340    15
10341    16
10342    17
10343    18
10344    19
10345    20
10346    21
10347    22
10348    23
10349    24
10350    25
10351    26
10352    27
10353    28
10354    29
10355    30
10356    31
10357    32
10358    33
10359    34
10360    35
10361    36
Name: index, dtype: int64
40926     1
40927     2
40928     3
40929     4


Name: index, dtype: int64
43806     1
43807     2
43808     3
43809     4
43810     5
43811     6
43812     7
43813     8
43814     9
43815    10
43816    11
43817    12
43818    13
43819    14
43820    15
43821    16
43822    17
43823    18
43824    19
43825    20
43826    21
43827    22
43828    23
43829    24
43830    25
43831    26
43832    27
43833    28
43834    29
43835    30
43836    31
43837    32
43838    33
43839    34
43840    35
43841    36
Name: index, dtype: int64
109722     1
109723     2
109724     3
109725     4
109726     5
109727     6
109728     7
109729     8
109730     9
109731    10
109732    11
109733    12
109734    13
109735    14
109736    15
109737    16
109738    17
109739    18
109740    19
109741    20
109742    21
109743    22
109744    23
109745    24
109746    25
109747    26
109748    27
109749    28
109750    29
109751    30
109752    31
109753    32
109754    33
109755    34
109756    35
109757    36
Name: index, dtype: int64
115842     1
115843   

113178     1
113179     2
113180     3
113181     4
113182     5
113183     6
113184     7
113185     8
113186     9
113187    10
113188    11
113189    12
113190    13
113191    14
113192    15
113193    16
113194    17
113195    18
113196    19
113197    20
113198    21
113199    22
113200    23
113201    24
113202    25
113203    26
113204    27
113205    28
113206    29
113207    30
113208    31
113209    32
113210    33
113211    34
113212    35
113213    36
Name: index, dtype: int64
110514     1
110515     2
110516     3
110517     4
110518     5
110519     6
110520     7
110521     8
110522     9
110523    10
110524    11
110525    12
110526    13
110527    14
110528    15
110529    16
110530    17
110531    18
110532    19
110533    20
110534    21
110535    22
110536    23
110537    24
110538    25
110539    26
110540    27
110541    28
110542    29
110543    30
110544    31
110545    32
110546    33
110547    34
110548    35
110549    36
Name: index, dtype: int64
46794     1


...

11308    1
11309    2
11310    3
Name: index, dtype: int64
13795    1
13796    2
13797    3
Name: index, dtype: int64
11805    1
11806    2
11807    3
Name: index, dtype: int64
12449    1
12450    2
12451    3
Name: index, dtype: int64
11693    1
11694    2
11695    3
Name: index, dtype: int64
14430    1
14431    2
14432    3
Name: index, dtype: int64
10219    1
10220    2
10221    3
Name: index, dtype: int64
11130    1
11131    2
11132    3
Name: index, dtype: int64
12038    1
12039    2
12040    3
Name: index, dtype: int64
12504    1
12505    2
12506    3
Name: index, dtype: int64
12138    1
12139    3
Name: index, dtype: int64
14010    1
14011    2
14012    3
Name: index, dtype: int64
12436    1
12437    2
12438    3
Name: index, dtype: int64
13584    1
13585    2
13586    3
Name: index, dtype: int64
11957    1
11958    3
Name: index, dtype: int64
11119    1
11120    2
11121    3
Name: index, dtype: int64
12434    1
12435    3
Name: index, dtype: int64
14329    1
14330    2
14331   

14718    1
14719    2
14720    3
Name: index, dtype: int64
12899    1
12900    2
12901    3
Name: index, dtype: int64
10809    1
10810    2
10811    3
Name: index, dtype: int64
14249    1
14250    3
Name: index, dtype: int64
14737    1
14738    2
14739    3
Name: index, dtype: int64
11768    1
11769    2
11770    3
Name: index, dtype: int64
13461    1
13462    2
13463    3
Name: index, dtype: int64
12836    1
12837    2
12838    3
Name: index, dtype: int64
11894    1
11895    2
11896    3
Name: index, dtype: int64
13421    1
13422    2
13423    3
Name: index, dtype: int64
9855    1
9856    2
9857    3
Name: index, dtype: int64
13545    1
13546    2
13547    3
Name: index, dtype: int64
14143    1
14144    2
14145    3
Name: index, dtype: int64
9873    1
9874    2
9875    3
Name: index, dtype: int64
14679    1
14680    2
14681    3
Name: index, dtype: int64
11526    1
11527    2
11528    3
Name: index, dtype: int64
14716    1
14717    3
Name: index, dtype: int64
12795    1
12796    3
Nam

Name: index, dtype: int64
13779    1
13780    2
13781    3
Name: index, dtype: int64
11354    1
11355    2
11356    3
Name: index, dtype: int64
12741    1
12742    2
12743    3
Name: index, dtype: int64
10638    1
10639    2
10640    3
Name: index, dtype: int64
14016    1
14017    2
14018    3
Name: index, dtype: int64
12271    1
12272    3
Name: index, dtype: int64
10457    1
10458    2
10459    3
Name: index, dtype: int64
14674    1
14675    3
Name: index, dtype: int64
11188    1
11189    2
11190    3
Name: index, dtype: int64
14710    1
14711    2
14712    3
Name: index, dtype: int64
9879    1
9880    3
Name: index, dtype: int64
14544    1
14545    2
14546    3
Name: index, dtype: int64
13131    1
13132    3
Name: index, dtype: int64
11699    1
11700    2
11701    3
Name: index, dtype: int64
12769    1
12770    2
12771    3
Name: index, dtype: int64
14519    1
14520    2
14521    3
Name: index, dtype: int64
10291    1
10292    2
10293    3
Name: index, dtype: int64
13446    1
13447 

Name: index, dtype: int64
10749    1
10750    2
10751    3
Name: index, dtype: int64
10813    1
10814    2
10815    3
Name: index, dtype: int64
11421    1
11422    3
Name: index, dtype: int64
11279    1
11280    2
11281    3
Name: index, dtype: int64
12928    1
12929    2
12930    3
Name: index, dtype: int64
10374    1
10375    2
10376    3
Name: index, dtype: int64
12047    1
12048    2
12049    3
Name: index, dtype: int64
14224    1
14225    2
14226    3
Name: index, dtype: int64
9669    1
9670    2
9671    3
Name: index, dtype: int64
13214    1
13215    2
13216    3
Name: index, dtype: int64
13399    1
13400    3
Name: index, dtype: int64
12778    1
12779    2
12780    3
Name: index, dtype: int64
9614    1
9615    2
9616    3
Name: index, dtype: int64
14243    1
14244    3
Name: index, dtype: int64
14205    1
14206    2
14207    3
Name: index, dtype: int64
12209    1
12210    2
12211    3
Name: index, dtype: int64
14511    1
14512    2
14513    3
Name: index, dtype: int64
9896    1


Name: index, dtype: int64
12152    1
12153    2
12154    3
Name: index, dtype: int64
12027    1
12028    2
12029    3
Name: index, dtype: int64
10960    1
10961    3
Name: index, dtype: int64
10334    1
10335    2
10336    3
Name: index, dtype: int64
13854    1
13855    2
13856    3
Name: index, dtype: int64
14342    1
14343    2
14344    3
Name: index, dtype: int64
11440    1
11441    2
11442    3
Name: index, dtype: int64
10288    1
10289    2
10290    3
Name: index, dtype: int64
9496    1
9497    2
9498    3
Name: index, dtype: int64
13401    1
13402    2
13403    3
Name: index, dtype: int64
10056    1
10057    2
10058    3
Name: index, dtype: int64
14200    1
14201    3
Name: index, dtype: int64
14826    1
14827    2
14828    3
Name: index, dtype: int64
10236    1
10237    2
10238    3
Name: index, dtype: int64
9491    1
9492    3
Name: index, dtype: int64
12456    1
12457    2
12458    3
Name: index, dtype: int64
13743    1
13744    2
13745    3
Name: index, dtype: int64
14008    

In [66]:
X_train = np.array(X_train)
X_test = np.array(X_test)
Y_train = np.array(Y_train)
Y_train = np.reshape(Y_train, (-1,4))
Y_test = np.array(Y_test)
Y_test = np.reshape(Y_test, (-1,4))

(X_train, X_valid) = X_train[50000:], X_train[:50000]
(Y_train, Y_valid) = Y_train[50000:], Y_train[:50000]


In [67]:
#removing first duplicate entry:
X_test = X_test[1:]

In [26]:
#Model
batch_size = 32
model = Sequential()
lstm_layer =LSTM(50, input_shape=(3, 19), activation='linear', dropout=0.25, recurrent_dropout=0.25, return_sequences=True)
lstm_layer.add_loss(1.0)
model.add(lstm_layer)
model.add(LeakyReLU(alpha=.001))
model.add(Dropout(0.5))
model.add(LSTM(50, return_sequences = True, activation="linear", dropout=0.25, recurrent_dropout=0.25))
model.add(LeakyReLU(alpha=.001))
model.add(Dropout(0.5))
model.add(LSTM(50, activation="linear", dropout=0.25, recurrent_dropout=0.25))
model.add(LeakyReLU(alpha=.001))
model.add(Dropout(0.5))

model.add(Dense(4))
model.add(LeakyReLU(alpha=.001))
adm = keras.optimizers.Adam(lr=0.0003, clipnorm=1.0)
model.compile(loss='mean_squared_error',
          optimizer= adm,
          metrics=['mse', 'mae'])
checkpointer = ModelCheckpoint(filepath='model.weights.best.hdf5', verbose=1, 
                               save_best_only=True)
model.fit(X_train, Y_train,
          batch_size=batch_size, validation_data=(X_valid, Y_valid),
          callbacks=[checkpointer], verbose=1, epochs=10)

Train on 193127 samples, validate on 50000 samples
Epoch 1/10
193127/193127 [==============================] - 112s 580us/step - loss: 1.9014 - mean_squared_error: 0.9014 - mean_absolute_error: 0.3372 - val_loss: 1.1849 - val_mean_squared_error: 0.1849 - val_mean_absolute_error: 0.2423
Epoch 2/10
193127/193127 [==============================] - 103s 533us/step - loss: 1.8037 - mean_squared_error: 0.8037 - mean_absolute_error: 0.2561 - val_loss: 1.4619 - val_mean_squared_error: 0.4619 - val_mean_absolute_error: 0.3120
Epoch 3/10
193127/193127 [==============================] - 104s 539us/step - loss: 1.7486 - mean_squared_error: 0.7486 - mean_absolute_error: 0.2186 - val_loss: 1.2097 - val_mean_squared_error: 0.2097 - val_mean_absolute_error: 0.2146
Epoch 4/10
193127/193127 [==============================] - 103s 535us/step - loss: 1.7307 - mean_squared_error: 0.7307 - mean_absolute_error: 0.2008 - val_loss: 1.1379 - val_mean_squared_error: 0.1379 - val_mean_absolute_error: 0.1939
Epoch

#### Timestamp, Mapping basin names, Water_per_foot nan values
### Experiments:
set timestamp --> boolean greater than or equal 2014.
removed entries that last more than 3 years (try training after three years isA)
dropped completion date  because they are all after 1/1/2014 so no difference in drilling techniques
To be done: try out normalizing the features data (0->1) 
Testing dataset have entries for more than three months and some have missing months entries

In [27]:
sum_liquid = np.zeros(len(X_test))
#sum of the non-standardized liquid for the first three months in the testing dataset
#and storing in the cumulative sum_liquid array (leih)
for i in range(3):
    cur_month = X_test[:, i, 0]
    cur_month = (cur_month * std_test_feat_arr[0]) + mean_test_feat_arr[0]
    sum_liquid += cur_month


In [28]:
counter = 4
### Predicting output
model.load_weights('model.weights.best.hdf5')

while(counter <= 36):
    Y_test = model.predict(X_test, batch_size=1)
    X_test_Next_Month = np.zeros((len(Y_test),19))
    # New month calculated
    sum_liquid += (Y_test[:,0] * std_test_feat_arr[0]) + mean_test_feat_arr[0]
    X_test_Next_Month[:, 0:4] = Y_test
    X_test_Next_Month[:, 4] = (counter - 18)/10.1
    X_test_Next_Month[:, 5:19] = X_test[:,0,5:19]
    #shifting the month entries in the X_test
    X_test[:,0:2,:] = X_test[:,1:3,:]
    X_test[:,2] = X_test_Next_Month
    print("Month", counter, "finished computing")
    counter += 1

Month 4 finished computing
Month 5 finished computing
Month 6 finished computing
Month 7 finished computing
Month 8 finished computing
Month 9 finished computing
Month 10 finished computing
Month 11 finished computing
Month 12 finished computing
Month 13 finished computing
Month 14 finished computing
Month 15 finished computing
Month 16 finished computing
Month 17 finished computing
Month 18 finished computing
Month 19 finished computing
Month 20 finished computing
Month 21 finished computing
Month 22 finished computing
Month 23 finished computing
Month 24 finished computing
Month 25 finished computing
Month 26 finished computing
Month 27 finished computing
Month 28 finished computing
Month 29 finished computing
Month 30 finished computing
Month 31 finished computing
Month 32 finished computing
Month 33 finished computing
Month 34 finished computing
Month 35 finished computing
Month 36 finished computing


In [ ]:
testing_apis = testing_apis[1:]
print(len(testing_apis))
mean_absolute_error = 0
sample_file['Id'] = (sample_file['Id']).astype(str)
sample_file['Id'] = sample_file['Id'].apply(lambda x: x.zfill(14))
idx = 0

for test in testing_apis:
#     print(sum_liquid[idx]- sample_file[sample_file['Id'] == test]['Predicted'])
    mean_absolute_error += abs(sum_liquid[idx] - sample_file[sample_file['Id'] == test]['Predicted'])/2586
    print(mean_absolute_error)
    idx += 1

In [77]:
mean_absolute_error

589   NaN
Name: Predicted, dtype: float64

In [36]:
sample_file[sample_file['Id'] == 5005072180000]

Id  Predicted
2158  5005072180000     613680